In [2]:
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import models, transforms
from torchvision.models import resnet50, ResNet50_Weights
from torch.utils.data import DataLoader, TensorDataset
from PIL import Image
import pandas as pd
import os
from pts_loader import load



In [3]:
image_dir = "Images/"
train_txt = "train_test_files/5_folders_cross_validations_files/cross_validation_1/train_1.txt"
test_txt = "train_test_files/5_folders_cross_validations_files/cross_validation_1/test_1.txt"



In [4]:
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),  
    transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])  # https://stackoverflow.com/questions/58151507/why-pytorch-officially-use-mean-0-485-0-456-0-406-and-std-0-229-0-224-0-2
])

In [5]:
def load_data(txt_file, image_dir):
    data = pd.read_csv(txt_file, delim_whitespace=True, header=None)
    image_paths = [image_dir + img_name for img_name in data[0]]
    scores = data[1].values
    return image_paths, scores

def create_dataloader(image_paths, scores, batch_size=64):
    images = []
    for img_path in image_paths:
        image = Image.open(img_path).convert('RGB')
        image = transform(image)
        print(image)
        images.append(image)

    images = torch.stack(images)
    scores = torch.tensor(scores, dtype=torch.float32)

    dataset = TensorDataset(images, scores)


    dataloader = DataLoader(dataset, batch_size=batch_size, shuffle=True)
    return dataloader

In [6]:
train_image_paths, train_scores = load_data(train_txt, image_dir)
test_image_paths, test_scores = load_data(test_txt, image_dir)

train_loader = create_dataloader(train_image_paths, train_scores)
test_loader = create_dataloader(test_image_paths, test_scores)

C:\Users\Валерий\AppData\Local\Temp\ipykernel_12692\729663538.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  data = pd.read_csv(txt_file, delim_whitespace=True, header=None)
C:\Users\Валерий\AppData\Local\Temp\ipykernel_12692\729663538.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  data = pd.read_csv(txt_file, delim_whitespace=True, header=None)


tensor([[[2.2489, 2.2489, 2.2489,  ..., 2.2489, 2.2489, 2.2489],
         [2.2489, 2.2489, 2.2489,  ..., 2.2489, 2.2489, 2.2489],
         [2.2489, 2.2489, 2.2489,  ..., 2.2489, 2.2489, 2.2489],
         ...,
         [2.2489, 2.2489, 2.2489,  ..., 2.2489, 2.2489, 2.2489],
         [2.2489, 2.2489, 2.2489,  ..., 2.2489, 2.2489, 2.2489],
         [2.2489, 2.2489, 2.2489,  ..., 2.2489, 2.2489, 2.2489]],

        [[2.4286, 2.4286, 2.4286,  ..., 2.4286, 2.4286, 2.4286],
         [2.4286, 2.4286, 2.4286,  ..., 2.4286, 2.4286, 2.4286],
         [2.4286, 2.4286, 2.4286,  ..., 2.4286, 2.4286, 2.4286],
         ...,
         [2.4286, 2.4286, 2.4286,  ..., 2.4286, 2.4286, 2.4286],
         [2.4286, 2.4286, 2.4286,  ..., 2.4286, 2.4286, 2.4286],
         [2.4286, 2.4286, 2.4286,  ..., 2.4286, 2.4286, 2.4286]],

        [[2.6400, 2.6400, 2.6400,  ..., 2.6400, 2.6400, 2.6400],
         [2.6400, 2.6400, 2.6400,  ..., 2.6400, 2.6400, 2.6400],
         [2.6400, 2.6400, 2.6400,  ..., 2.6400, 2.6400, 2.

In [7]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = resnet50(ResNet50_Weights)
# model = torch.nn.DataParallel(model)

# # Set the model to run on the device
num_ftrs = model.fc.in_features
model.fc = nn.Linear(num_ftrs, 1)
# model.load_state_dict(torch.load("resnet18_finetuned.pth"))
# model.eval()
model = model.to(device)



c:\Users\Валерий\AppData\Local\Programs\Python\Python312\Lib\site-packages\torchvision\models\_utils.py:135: UserWarning: Using 'weights' as positional parameter(s) is deprecated since 0.13 and may be removed in the future. Please use keyword parameter(s) instead.
  warnings.warn(
c:\Users\Валерий\AppData\Local\Programs\Python\Python312\Lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


In [8]:
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

In [9]:
def train_model(num_epochs = 10):
    for epoch in range(num_epochs):
        model.train()
        running_loss = 0.0
        
        progress = 0
        for inputs, targets in train_loader:
            progress += 1
            print(f'Progress: {progress}/{len(train_loader)}', end='\r')
            optimizer.zero_grad()
            inputs = inputs.to(device)
            targets = targets.to(device)
            outputs = model(inputs)
            loss = criterion(outputs.squeeze(), targets)
            loss.backward()
            optimizer.step()

            running_loss += loss.item() * inputs.size(0)

        epoch_loss = running_loss / len(train_loader.dataset)
        print(f'Epoch {epoch+1}/{num_epochs}, Loss: {epoch_loss:.4f}')
        

    model.eval()

def test_model():
    with torch.no_grad():
        running_loss = 0.0
        for inputs, targets in test_loader:
            inputs = inputs.to(device)
            targets = targets.to(device)
            outputs = model(inputs)
            loss = criterion(outputs.squeeze(), targets)
            running_loss += loss.item() * inputs.size(0)

    test_loss = running_loss / len(test_loader.dataset)
    print(f'Test Loss: {test_loss:.4f}')

train_model(6)
test_model()



Epoch 1/6, Loss: 0.5822
Epoch 2/6, Loss: 0.1568
Epoch 3/6, Loss: 0.1172
Epoch 4/6, Loss: 0.1017
Epoch 5/6, Loss: 0.0782
Epoch 6/6, Loss: 0.0676
Test Loss: 0.1116


In [13]:
torch.save(model.state_dict(), 'resnet50_finetuned.pth')


In [11]:
manual_check_dir = "ManualCheck/"
# print(os.listdir(manual_check_dir))

def PrintBeauty(dir_path):
    for img_path in os.listdir(dir_path):
        image = Image.open(dir_path + img_path).convert('RGB')
        image = transform(image)
        print(model(image.unsqueeze(0).to(device)).item())

PrintBeauty(manual_check_dir)



3.0234038829803467
3.686040163040161
3.8593318462371826


In [12]:
# print(load("facial landmark/AF1.pts"))

ValueError: '{' is not in list